<a href="https://colab.research.google.com/github/ouhenio/miniDALL-E_notebook/blob/main/minDALLE.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **miniDALL-E**

Generate images from text prompts using [minDALL-E on Conceptual Captions](https://github.com/kakaobrain/minDALL-E), a model created by Saehoon Kim, Sanghun Cho, Chiheon Kim, Doyup Lee, and Woonhyuk Baek.


In [1]:
#@markdown #**Install libraries** 🏗️
# @markdown This cell will take a little while because it has to download several libraries.

#@markdown ---

!git clone https://github.com/kakaobrain/minDALL-E.git
import sys
sys.path.append('./minDALL-E')
%pip install -q -r minDALL-E/requirements.txt
%pip install -q pytorch-lightning omegaconf einops tokenizers
%pip install -q git+https://github.com/openai/CLIP.git
!pip install torch==1.8.1 torchvision==0.9.1 torchtext==0.9.1 -f https://download.pytorch.org/whl/cu101/torch_stable.html

Cloning into 'minDALL-E'...
remote: Enumerating objects: 86, done.
remote: Counting objects: 100% (86/86), done.
remote: Compressing objects: 100% (80/80), done.
remote: Total 86 (delta 9), reused 76 (delta 5), pack-reused 0
Unpacking objects: 100% (86/86), done.
     |████████████████████████████████| 735.5 MB 15 kB/s 
     |████████████████████████████████| 3.3 MB 53.3 MB/s 
     |████████████████████████████████| 69 kB 9.0 MB/s 
     |████████████████████████████████| 525 kB 64.4 MB/s 
     |████████████████████████████████| 74 kB 3.7 MB/s 
     |████████████████████████████████| 64 kB 3.5 MB/s 
     |████████████████████████████████| 23.3 MB 1.6 MB/s 
     |████████████████████████████████| 22.1 MB 1.3 MB/s 
     |████████████████████████████████| 22.1 MB 1.3 MB/s 
     |████████████████████████████████| 17.4 MB 19.6 MB/s 
     |████████████████████████████████| 17.3 MB 25 kB/s 
     |████████████████████████████████| 829 kB 55.5 MB/s 
     |████████████████████████████████| 132 kB

In [2]:
#@markdown #**Check GPU type** 🕵️
#@markdown ### Factory reset runtime if you don't have the desired GPU.

#@markdown ---




#@markdown V100 = Excellent (*Available only for Colab Pro users*)

#@markdown P100 = Very Good

#@markdown T4 = Good (*preferred*)

#@markdown K80 = Bad

#@markdown P4 = (*Not Recommended*) 

#@markdown ---

!nvidia-smi -L

GPU 0: Tesla P100-PCIE-16GB (UUID: GPU-81938932-6313-bab9-f368-6ed6520f8c76)


In [2]:
#@markdown #**Define necessary functions** 🛠️

%cd minDALL-E

import os
import sys
import math
import argparse
import clip
import numpy as np
%matplotlib inline
import matplotlib.pyplot as plt
from PIL import Image

import ipywidgets as widgets
from IPython.display import display
from IPython.display import clear_output

output = widgets.Output()
plot_output = widgets.Output()

sys.path.append(os.path.dirname(os.getcwd()))

from dalle.models import Dalle
from dalle.utils.utils import set_seed, clip_score

device = 'cuda:0'
model = Dalle.from_pretrained("minDALL-E/1.3B")
model_clip, preprocess_clip = clip.load("ViT-B/32", device=device)

model_clip.to(device=device)
model.to(device=device)

def sampling(prompt, top_k, softmax_temperature, seed, num_candidates=96, num_samples_for_display=36):
    # Setup
    n_row = int(math.sqrt(num_samples_for_display))
    n_col = int(math.sqrt(num_samples_for_display))
    set_seed(seed)
    
    # Sampling
    images = model.sampling(prompt=prompt,
                            top_k=top_k,
                            top_p=None,
                            softmax_temperature=softmax_temperature,
                            num_candidates=num_candidates,
                            device=device).cpu().numpy()
    images = np.transpose(images, (0, 2, 3, 1))

    # CLIP Re-ranking
    rank = clip_score(prompt=prompt, images=images, model_clip=model_clip, preprocess_clip=preprocess_clip, device=device)
    images = images[rank]
    
    images = images[:num_samples_for_display]
    fig = plt.figure(figsize=(8*n_row, 8*n_col))

    for i in range(num_samples_for_display):
        ax = fig.add_subplot(n_row, n_col, i+1)
        ax.imshow(images[i])
        ax.set_axis_off()

    plt.tight_layout()
    plt.show()

/content/minDALL-E


100%|█████████████████████████████████████| 4.72G/4.72G [03:36<00:00, 23.4MiB/s]
extracting: ./1.3B/tokenizer/bpe-16k-vocab.json (size:0MB): 100%|██████████| 7/7 [00:49<00:00,  7.05s/it]


/root/.cache/minDALL-E/1.3B/tokenizer successfully restored..
/root/.cache/minDALL-E/1.3B/stage1_last.ckpt successfully restored..
/root/.cache/minDALL-E/1.3B/stage2_last.ckpt succesfully restored..


100%|████████████████████████████████████████| 338M/338M [00:02<00:00, 172MiB/s]


In [4]:
#@markdown #**Parameters** ✍️

text = "a painting of the seashore under a starry night with full moon"#@param {type:"string"}
temp = 1#@param {type:"number"}
seed = 0#@param {type:"number"}
top_k = 256#@param {type:"number"}

In [6]:
#@markdown #**Run model** 🚀

output.clear_output()
plot_output.clear_output()
with plot_output:
    sampling(prompt=text, 
        top_k=top_k,
        softmax_temperature=temp,
        seed=seed,
        num_candidates=16,
        num_samples_for_display=16)

display(output)
display(plot_output)

Output()

Output()